# EDA on Clean Data 
    



## 1.Importing all the packages, modules

In [11]:
import pandas as pd
import numpy as np
import datetime, time
import glob
import csv
import re
import json
import boto
import boto.s3
from boto.s3.key import Key
from boto.s3.cors import CORSConfiguration
import glob
import boto3
import botocore
import csv
import re
import json
import os
import sys
from scipy import interpolate
flag = 0
tempFullDataList =[]
tempSODDataList =[]

print("Step1 -Import Done ")

Step1 -Import Done 


In [12]:
#fetching the timestamp
ts = time.time()
st = datetime.datetime.fromtimestamp(ts).strftime('%d%m%y%M%S')
st1 = datetime.datetime.fromtimestamp(ts).strftime('%d%m%y')

In [13]:
# Create logfile.
logfile = open(st+".txt", "a")
def log_entry(s):
    #print('Date now: %s' % datetime.datetime.now())

    timestamp = '[%s] : ' % datetime.datetime.now()
    log_line = timestamp + s + '\n'
    logfile.write(log_line)
    logfile.flush()
log_entry("Import Done")

In [14]:
with open('configWrangle.json') as data_file:    
    configdata = json.load(data_file)
log_entry("Raw Data Link from config file: "+configdata["cleanData"])
clean_link=configdata["cleanData"]

In [15]:
# connect to AWS
AWS_ACCESS_KEY_ID = configdata["AWSAccess"]
print(AWS_ACCESS_KEY_ID)
AWS_SECRET_ACCESS_KEY = configdata["AWSSecret"]
print(AWS_SECRET_ACCESS_KEY)
TeamNumber=configdata["team"]
conn = boto.connect_s3(AWS_ACCESS_KEY_ID, AWS_SECRET_ACCESS_KEY)
s3 = boto3.resource('s3', aws_access_key_id=AWS_ACCESS_KEY_ID, aws_secret_access_key=AWS_SECRET_ACCESS_KEY)

AKIAIBFJOEIBO63CKYHm
4NRpHtvqR7NYhiHFgZXldGyx6o9NY6IJTlJKLHB1


In [16]:
status= os.path.exists(clean_link)
print status

True


In [17]:
if status==True:
    file=clean_link
    print("File found on Local")
    log_entry("File found on Local")
elif status==False:
    file=clean_link
    bucket_name = str(TeamNumber) + configdata["state"].lower() + 'assignment1_clean'
    my_bucket = conn.get_bucket(bucket_name, validate=False)
    print my_bucket
    k = Key(my_bucket)
    exists = False

    try:
        s3.Object(bucket_name, file).load()
    except botocore.exceptions.ClientError as e:
        if e.response['Error']['Code'] == "404":
            exists = False
        else:
            raise
    else:
        exists = True
    
    if exists==False:
        print("File not found.")
        log_entry("File not found.")
    elif exists==True:
        print("File exists.")
        log_entry("File exists.")
        cors_cfg = CORSConfiguration()
        cors_cfg.add_rule(['PUT', 'POST', 'DELETE'], 'https://www.example.com', allowed_header='*', max_age_seconds=3000, expose_header='x-amz-server-side-encryption')
        cors_cfg.add_rule('GET', '*')
        k = my_bucket.get_key(file, validate=False)
        my_bucket.set_cors(cors_cfg)
        k.get_contents_to_filename(clean_link)
        print k.last_modified
        log_entry(file+" has been uploaded to "+bucket_name)
        print("File Downloaded.")
        log_entry("File downloaded from S3 bucket.")
        file=clean_link


File found on Local


In [18]:
file1=file
a=pd.read_csv(file1,sep=',', error_bad_lines=False, index_col=False, dtype='unicode',parse_dates=["DATE"])
for i,x in a.iterrows():
         if(x['REPORTTPYE'] != 'SOD'):
                tempFullDataList.append(x)
         elif(x['REPORTTPYE'] =='SOD'):
                tempSODDataList.append(x)
                
print("Step 2 Loading CSV File Done")

Step 2 Loading CSV File Done


## EAD 

## Getting the Latest Date for One Day Analysis 

In [19]:
v = a.tail(2)['DATE'][:-1]
for i in v:
    latestDate=str(i).split()[0].split('-')[2]
print("LatestDate "+latestDate)
dataHours =a

LatestDate 20


In [20]:
dataframeHours = pd.DataFrame(dataHours.tail(48)[:-1])
dateATemp = {'Temperature':[],'Time':[]}
for x,i in dataframeHours.iterrows():
# Moving to Seperate Dictionary to Analyse it 
      if(str(i['DATE']).split()[0].split('-')[2]==latestDate):
                dateATemp['Time'].append(str(i['DATE']).split()[1].split(':')[0])
                dateATemp['Temperature'].append(str(i['HOURLYDRYBULBTEMPC']))

In [21]:
## Relationship between Temperature and DEw Point 

In [22]:
from bokeh.plotting  import figure,output_file, show
p=figure(width=2500,height=500,x_axis_type="datetime")
p.line(a["DATE"],a["HOURLYDRYBULBTEMPC"],color="Orange",alpha=0.5)
p.line(a["DATE"],a["HOURLYDewPointTempC"],color="Green",alpha=0.5)
p.xaxis.axis_label="TimeLine"
p.yaxis.axis_label="TEmperature in C"
show(p)


 

In [23]:
## Latest DAy Temperature Analysis 

In [24]:
from bokeh.io import output_file, show
from bokeh.charts import Scatter
import bokeh.plotting as bk
from bokeh.plotting import figure 
bk.output_notebook()
plot = figure(plot_width=600,plot_height=200,tools ='pan,box_zoom')
 
p = Scatter(dateATemp,x="Time",y="Temperature",xlabel="Hours",ylabel="Temperature in C ")

bk.show(p)

Loading BokehJS ...

In [25]:
## Relationship between HOURLYSeaLevelPressure, HOURLYAltimeterSetting and HOURLYStationPressure

In [26]:
from bokeh.plotting  import figure,output_file, show
p=figure(width=2500,height=500,x_axis_type="datetime")
p.line(a["DATE"],a["HOURLYSeaLevelPressure"],color="Orange",alpha=0.5)
p.line(a["DATE"],a["HOURLYAltimeterSetting"],color="Green",alpha=0.5)
p.line(a["DATE"],a["HOURLYStationPressure"],color="yellow",alpha=0.5)
p.xaxis.axis_label="TimeLine"
p.yaxis.axis_label="TEmperature in C"
show(p)

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.


In [27]:
## Plotting of relative Humidity 

In [28]:
from bokeh.plotting  import figure,output_file, show
p=figure(width=2500,height=500,x_axis_type="datetime")
p.line(a["DATE"],a["HOURLYRelativeHumidity"],color="indigo",alpha=0.5)
p.xaxis.axis_label="TimeLine"
p.yaxis.axis_label="TEmperature in C"
show(p)

In [29]:
## Wind Speed along the years 

In [30]:
from bokeh.plotting  import figure,output_file, show
p=figure(width=2500,height=500,x_axis_type="datetime")
p.line(a["DATE"],a["HOURLYWindSpeed"],color="dodgerblue",alpha=0.5)
p.xaxis.axis_label="TimeLine"
p.yaxis.axis_label="TEmperature in C"
show(p)